In [1]:
# Importing Libraries
from sklearnex import patch_sklearn #Improves sklearn alghoritms performance
patch_sklearn()
import sklearn
print('scikit-learn version\n', sklearn.__version__)
from sklearn.model_selection import ParameterGrid, GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.multiclass import OutputCodeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import LinearSVC
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import ComplementNB
import pickle
import pandas as pd
import numpy as np

scikit-learn version
 1.0.2


Intel(R) Extension for Scikit-learn* enabled (https://github.com/intel/scikit-learn-intelex)


In [2]:
#Set seed
seed=41

In [3]:
classif_level = 2

# Load Data

In [4]:
feature_names = pickle.load(open('Dataset/feature_names.pkl', 'rb'))
X_train = pickle.load(open(f'Dataset/X_train.pkl', 'rb'))
X_train_scal = pickle.load(open(f'Dataset/X_train_scal.pkl', 'rb'))
y_train = pickle.load(open(f'Dataset/y_train.pkl', 'rb'))
#all Superclasses
sclasses = pickle.load(open('Dataset/all_categories.pkl', 'rb'))['Superclass']
#Superclasses with unique child
sc_u = pickle.load(open(f'Dataset/SC_wunique_child.pkl', 'rb'))

In [5]:
for i, sclass in enumerate(sclasses):
    print(i, sclass)

0 Acetylides
1 Alkaloids and derivatives
2 Allenes
3 Benzenoids
4 Homogeneous metal compounds
5 Homogeneous non-metal compounds
6 Hydrocarbon derivatives
7 Hydrocarbons
8 Lignans, neolignans and related compounds
9 Lipids and lipid-like molecules
10 Miscellaneous inorganic compounds
11 Mixed metal/non-metal compounds
12 Nucleosides, nucleotides, and analogues
13 Organic 1,3-dipolar compounds
14 Organic Polymers
15 Organic acids and derivatives
16 Organic compounds - Unspecified
17 Organic nitrogen compounds
18 Organic oxygen compounds
19 Organic salts
20 Organohalogen compounds
21 Organoheterocyclic compounds
22 Organometallic compounds
23 Organophosphorus compounds
24 Organosulfur compounds
25 Phenylpropanoids and polyketides


## Train and Tune classifiers

### Random Forests

In [ ]:
for i, sclass in enumerate(sclasses):
    print(sclass)
    if sclass in sc_u:
        print('Only one subchild')
        continue
    for f_sel in ['all', 'sel']:
        print(f_sel)
        if f_sel == 'sel':
            sel_f = pickle.load(open('Results/selected_features.pkl', 'rb'))['Class'][sclass]['selected features']
            f_index = [feature_names.index(feature) for feature in sel_f]
            X_train_ = X_train[y_train[:, classif_level-1]==sclass][:, f_index]
            grid = {'class_weight': [None, 'balanced', 'balanced_subsample'],
                'criterion' : ['gini', 'entropy'],
                'max_features' : range(1, len(sel_f)+1)}
        else:
            X_train_ = X_train[y_train[:, classif_level-1]==sclass]
            grid = {'class_weight': [None, 'balanced', 'balanced_subsample'],
                'criterion' : ['gini', 'entropy'],
                'max_features' : [1, 2, 3, 5, 7, 10, 15, 20, 30, 40, 50, 60, 70, 80, 90, 100, 110, 120, 130, 133]}
        y_train_ = y_train[y_train[:, classif_level-1]==sclass][:, classif_level]
        
        estimator = RandomForestClassifier(random_state=seed, n_jobs=-1, n_estimators=200)
        gs = GridSearchCV(estimator, param_grid=grid, scoring=['f1_macro', 'f1_micro'], refit='f1_macro', cv=3, verbose=3, 
                          error_score='raise', return_train_score=True, n_jobs=-1)
        gs.fit(X_train_, y_train_)
        pickle.dump(gs, open(f'Models/Class/{i}_RF_{f_sel}_feat.pkl', 'wb'))

In [32]:
for i, sclass in enumerate(sclasses):
    print(sclass)
    if sclass in sc_u:
        continue
    for f_sel in ['all', 'sel']:
        print(f_sel)
        gs = pickle.load(open(f'Models/Class/{i}_RF_{f_sel}_feat.pkl', 'rb'))
        print('f1_macro_val ->', gs.cv_results_['mean_test_f1_macro'][gs.best_index_])
        print('f1_macro_train ->', gs.cv_results_['mean_train_f1_macro'][gs.best_index_])
        print('f1_micro_val ->', gs.cv_results_['mean_test_f1_micro'][gs.best_index_])
        print('f1_micro_train ->', gs.cv_results_['mean_train_f1_micro'][gs.best_index_])

Inorganic compounds
all
f1_macro_test -> 0.7512662834981398
f1_macro_train -> 0.8090408627873611
f1_micro_test -> 0.9174552935591075
f1_micro_train -> 0.9601282330645854
sel
f1_macro_test -> 0.7497080376873996
f1_macro_train -> 0.8816896545003239
f1_micro_test -> 0.923078546183468
f1_micro_train -> 0.9746729792727297
Organic compounds
all
f1_macro_test -> 0.5202564530455621
f1_macro_train -> 0.8395686699909547
f1_micro_test -> 0.8776570423263997
f1_micro_train -> 0.9514979819931698
sel
f1_macro_test -> 0.5258085250500398
f1_macro_train -> 0.826792738664746
f1_micro_test -> 0.8783193625168167
f1_micro_train -> 0.9503233985304771


### KNN

In [14]:
grid = {'n_neighbors': range(1, 31), 'weights' : ['uniform', 'distance'],
        'metric':['manhattan', 'euclidean', 'cosine']}

In [16]:
for i, sclass in enumerate(sclasses):
    print(sclass)
    if sclass in sc_u:
        print('Only one subchild')
        continue
    for f_sel in ['all', 'sel']:
        print(f_sel)
        grid['n_neighbors'] = range(1, 31)
        if f_sel == 'sel':
            sel_f = pickle.load(open('Results/selected_features.pkl', 'rb'))['Class'][sclass]['selected features']
            f_index = [feature_names.index(feature) for feature in sel_f]
            X_train_ = X_train_scal[y_train[:, classif_level-1]==sclass][:, f_index]
        else:
            X_train_ = X_train_scal[y_train[:, classif_level-1]==sclass]
        y_train_ = y_train[y_train[:, classif_level-1]==sclass][:, classif_level]
        n_samples = int(len(y_train_)*2/3)
        if n_samples<30:
            grid['n_neighbors'] = range(1, n_samples + 1)
        estimator = KNeighborsClassifier(algorithm = 'brute', n_jobs=-1)
        gs = GridSearchCV(estimator, param_grid=grid, scoring=['f1_macro', 'f1_micro'], refit='f1_macro', cv=3, verbose=3, 
                          error_score='raise', return_train_score=True, n_jobs=10)
        gs.fit(X_train_, y_train_)
        pickle.dump(gs, open(f'Models/Class/{i}_KNN_{f_sel}_feat.pkl', 'wb'))

Acetylides
Only one subchild
Alkaloids and derivatives
Allenes
Only one subchild
Benzenoids
Homogeneous metal compounds
Homogeneous non-metal compounds
Hydrocarbon derivatives
Hydrocarbons
Lignans, neolignans and related compounds
Lipids and lipid-like molecules
Miscellaneous inorganic compounds
Only one subchild
Mixed metal/non-metal compounds
Nucleosides, nucleotides, and analogues
Organic 1,3-dipolar compounds
Organic Polymers
Organic acids and derivatives
Organic compounds - Unspecified
Only one subchild
Organic nitrogen compounds
Only one subchild
Organic oxygen compounds
Organic salts
Only one subchild
Organohalogen compounds
all
Fitting 3 folds for each of 180 candidates, totalling 540 fits


/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A

/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A

/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A

/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A

...

/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A

/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  result = super(NeighborsBase, self)._fit(X, y)
/home/hsilva/anaconda3/lib/python3.9/site-packages/daal4py/sklearn/neighbors/_base.py:357: DataConversionWarning: A

[CV 2/3] END metric=euclidean, n_neighbors=19, weights=uniform; f1_macro: (train=0.303, test=0.293) f1_micro: (train=0.677, test=0.647) total time=   0.2s
[CV 1/3] END metric=euclidean, n_neighbors=23, weights=distance; f1_macro: (train=0.130, test=0.102) f1_micro: (train=0.199, test=0.175) total time=   0.2s
[CV 2/3] END metric=euclidean, n_neighbors=24, weights=distance; f1_macro: (train=0.113, test=0.077) f1_micro: (train=0.211, test=0.134) total time=   0.2s
[CV 3/3] END metric=euclidean, n_neighbors=25, weights=distance; f1_macro: (train=0.112, test=0.093) f1_micro: (train=0.207, test=0.163) total time=   0.4s
[CV 2/3] END metric=euclidean, n_neighbors=27, weights=uniform; f1_macro: (train=0.263, test=0.244) f1_micro: (train=0.658, test=0.641) total time=   0.3s
[CV 3/3] END metric=euclidean, n_neighbors=28, weights=distance; f1_macro: (train=0.097, test=0.081) f1_micro: (train=0.194, test=0.153) total time=   0.3s
[CV 1/3] END metric=euclidean, n_neighbors=30, weights=distance; f

[CV 2/3] END metric=euclidean, n_neighbors=10, weights=distance; f1_macro: (train=0.241, test=0.144) f1_micro: (train=0.343, test=0.246) total time=   0.2s
[CV 1/3] END metric=euclidean, n_neighbors=17, weights=distance; f1_macro: (train=0.160, test=0.166) f1_micro: (train=0.234, test=0.233) total time=   0.2s
[CV 1/3] END metric=euclidean, n_neighbors=18, weights=uniform; f1_macro: (train=0.304, test=0.286) f1_micro: (train=0.674, test=0.650) total time=   0.1s
[CV 3/3] END metric=euclidean, n_neighbors=18, weights=distance; f1_macro: (train=0.134, test=0.122) f1_micro: (train=0.257, test=0.200) total time=   0.1s
[CV 2/3] END metric=euclidean, n_neighbors=19, weights=distance; f1_macro: (train=0.146, test=0.101) f1_micro: (train=0.249, test=0.153) total time=   0.2s
[CV 1/3] END metric=euclidean, n_neighbors=20, weights=distance; f1_macro: (train=0.138, test=0.100) f1_micro: (train=0.214, test=0.201) total time=   0.1s
[CV 1/3] END metric=euclidean, n_neighbors=21, weights=distance; 

[CV 1/3] END metric=euclidean, n_neighbors=30, weights=uniform; f1_macro: (train=0.259, test=0.241) f1_micro: (train=0.654, test=0.635) total time=   0.9s
[CV 2/3] END metric=cosine, n_neighbors=2, weights=distance; f1_macro: (train=0.703, test=0.423) f1_micro: (train=0.802, test=0.642) total time=   1.0s
[CV 2/3] END metric=cosine, n_neighbors=4, weights=uniform; f1_macro: (train=0.485, test=0.373) f1_micro: (train=0.726, test=0.644) total time=   1.6s
[CV 2/3] END metric=cosine, n_neighbors=5, weights=distance; f1_macro: (train=0.728, test=0.396) f1_micro: (train=0.820, test=0.664) total time=   1.4s
[CV 3/3] END metric=cosine, n_neighbors=7, weights=uniform; f1_macro: (train=0.430, test=0.344) f1_micro: (train=0.709, test=0.652) total time=   1.1s
[CV 2/3] END metric=cosine, n_neighbors=8, weights=distance; f1_macro: (train=0.731, test=0.400) f1_micro: (train=0.826, test=0.669) total time=   1.3s
[CV 2/3] END metric=cosine, n_neighbors=10, weights=uniform; f1_macro: (train=0.384, te

In [10]:
for i, sclass in enumerate(sclasses):
    print(sclass)
    if sclass in sc_u:
        continue
    for f_sel in ['all', 'sel']:
        print(f_sel)
        gs = pickle.load(open(f'Models/Class/{i}_KNN_{f_sel}_feat.pkl', 'rb'))
        print('f1_macro_test ->', gs.cv_results_['mean_test_f1_macro'][gs.best_index_])
        print('f1_macro_train ->', gs.cv_results_['mean_train_f1_macro'][gs.best_index_])
        print('f1_micro_test ->', gs.cv_results_['mean_test_f1_micro'][gs.best_index_])
        print('f1_micro_train ->', gs.cv_results_['mean_train_f1_micro'][gs.best_index_])

Inorganic compounds
all
f1_macro_test -> 0.6255606221065472
f1_macro_train -> 0.6935180897124114
f1_micro_test -> 0.8311257055441262
f1_micro_train -> 0.8841451899394491
GridSearchCV(cv=3, error_score='raise',
             estimator=KNeighborsClassifier(n_jobs=-1), n_jobs=-1,
             param_grid=[{'algorithm': ['ball_tree', 'kd_tree'],
                          'leaf_size': range(10, 51, 5),
                          'n_neighbors': range(1, 11), 'p': [1, 2],
                          'weights': ['uniform', 'distance']},
                         {'algorithm': ['brute'], 'n_neighbors': range(1, 11),
                          'p': [1, 2], 'weights': ['uniform', 'distance']}],
             refit='f1_macro', return_train_score=True,
             scoring=['f1_macro', 'f1_micro'], verbose=3)
sel
f1_macro_test -> 0.6498634367585566
f1_macro_train -> 0.7850997520279942
f1_micro_test -> 0.7467188901197447
f1_micro_train -> 0.8911768784295081
GridSearchCV(cv=3, error_score='raise',
          

### Logistic Regression

In [95]:
grid = [{'penalty': ['l1'],
         'C': [0.01, 0.1, 1, 10, 100],
         'fit_intercept': [True, False],
         'class_weight': [None, 'balanced'],
         'multi_class':['ovr', 'multinomial'],
         'solver': ['saga']},
        {'penalty': ['elasticnet'],
         'C': [0.01, 0.1, 1, 10, 100],
         'fit_intercept': [True, False],
         'class_weight': [None, 'balanced'],
         'multi_class':['ovr', 'multinomial'],
         'l1_ratio': [0.25, 0.5, 0.75],
         'solver': ['saga']},
        {'penalty': ['l2'],
         'C': [0.01, 0.1, 1, 10, 100],
         'fit_intercept': [True, False],
         'class_weight': [None, 'balanced'],
         'multi_class':['ovr', 'multinomial'],
         'solver': ['sag', 'saga']},
       {'penalty': ['none'],
         'fit_intercept': [True, False],
         'class_weight': [None, 'balanced'],
         'multi_class':['ovr', 'multinomial'],
         'solver': ['sag', 'saga']}]

In [ ]:
for i, sclass in enumerate(sclasses):
    print(sclass)
    if sclass in sc_u:
        print('Only one subchild')
        continue
    if i in [9, 15, 21, 25]:
        max_iter = 100
    else:
        max_iter = 5000
    for f_sel in ['all', 'sel']:
        print(f_sel)
        if f_sel == 'sel':
            sel_f = pickle.load(open('Results/selected_features.pkl', 'rb'))['Class'][sclass]['selected features']
            f_index = [feature_names.index(feature) for feature in sel_f]
            X_train_ = X_train_scal[y_train[:, classif_level-1]==sclass][:, f_index]
        else:
            X_train_ = X_train_scal[y_train[:, classif_level-1]==sclass]
            
        y_train_ = y_train[y_train[:, classif_level-1]==sclass][:, classif_level]
        
        estimator = LogisticRegression(max_iter=max_iter, tol=1e-6, random_state=seed, n_jobs=-1)
        gs = GridSearchCV(estimator, param_grid=grid, scoring=['f1_macro', 'f1_micro'], refit='f1_macro', cv=3,
                          error_score='raise', return_train_score=True, n_jobs=-1)
        gs.fit(X_train_, y_train_)
        pickle.dump(gs, open(f'Models/Class/{i}_LR_{f_sel}_feat.pkl', 'wb'))

Fitting 3 folds for each of 1080 candidates, totalling 3240 fits
[CV 1/3] END C=0.1, class_weight=None, fit_intercept=True, multi_class=ovr, penalty=l1, solver=saga, tol=1e-05; f1_macro: (train=0.177, test=0.176) f1_micro: (train=0.546, test=0.545) total time=   0.2s
[CV 2/3] END C=0.1, class_weight=None, fit_intercept=True, multi_class=ovr, penalty=l1, solver=saga, tol=1e-05; f1_macro: (train=0.177, test=0.177) f1_micro: (train=0.546, test=0.546) total time=   0.1s
[CV 3/3] END C=0.1, class_weight=None, fit_intercept=True, multi_class=ovr, penalty=l1, solver=saga, tol=1e-05; f1_macro: (train=0.177, test=0.177) f1_micro: (train=0.546, test=0.546) total time=   0.1s
[CV 1/3] END C=0.1, class_weight=None, fit_intercept=True, multi_class=ovr, penalty=l1, solver=saga, tol=0.0001; f1_macro: (train=0.177, test=0.176) f1_micro: (train=0.546, test=0.545) total time=   0.1s
[CV 2/3] END C=0.1, class_weight=None, fit_intercept=True, multi_class=ovr, penalty=l1, solver=saga, tol=0.0001; f1_macro:

/home/hsilva/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV 1/3] END C=0.1, class_weight=balanced, fit_intercept=True, multi_class=ovr, penalty=l1, solver=saga, tol=1e-05; f1_macro: (train=0.542, test=0.516) f1_micro: (train=0.737, test=0.756) total time=   7.8s


/home/hsilva/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV 2/3] END C=0.1, class_weight=balanced, fit_intercept=True, multi_class=ovr, penalty=l1, solver=saga, tol=1e-05; f1_macro: (train=0.573, test=0.523) f1_micro: (train=0.750, test=0.752) total time=   7.7s


...

[CV 3/3] END C=2, class_weight=balanced, fit_intercept=False, multi_class=multinomial, penalty=l1, solver=saga, tol=0.0001; f1_macro: (train=0.728, test=0.641) f1_micro: (train=0.854, test=0.808) total time=  18.6s


/home/hsilva/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV 1/3] END C=2, class_weight=balanced, fit_intercept=False, multi_class=multinomial, penalty=l1, solver=saga, tol=0.001; f1_macro: (train=0.648, test=0.668) f1_micro: (train=0.799, test=0.787) total time=  18.9s


/home/hsilva/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV 2/3] END C=2, class_weight=balanced, fit_intercept=False, multi_class=multinomial, penalty=l1, solver=saga, tol=0.001; f1_macro: (train=0.698, test=0.647) f1_micro: (train=0.841, test=0.820) total time=  18.8s
[CV 3/3] END C=2, class_weight=balanced, fit_intercept=False, multi_class=multinomial, penalty=l1, solver=saga, tol=0.001; f1_macro: (train=0.728, test=0.641) f1_micro: (train=0.854, test=0.808) total time=  11.4s
[CV 1/3] END C=3, class_weight=None, fit_intercept=True, multi_class=ovr, penalty=l1, solver=saga, tol=1e-05; f1_macro: (train=0.747, test=0.606) f1_micro: (train=0.901, test=0.868) total time=   8.1s
[CV 2/3] END C=3, class_weight=None, fit_intercept=True, multi_class=ovr, penalty=l1, solver=saga, tol=1e-05; f1_macro: (train=0.657, test=0.597) f1_micro: (train=0.909, test=0.856) total time=   8.4s
[CV 3/3] END C=3, class_weight=None, fit_intercept=True, multi_class=ovr, penalty=l1, solver=saga, tol=1e-05; f1_macro: (train=0.731, test=0.608) f1_micro: (train=0.899, 

In [7]:
for i, sclass in enumerate(sclasses):
    print(sclass)
    if sclass in sc_u:
        continue
    for f_sel in ['all', 'sel']:
        print(f_sel)
        gs = pickle.load(open(f'Models/Class/{i}_LR_{f_sel}_feat.pkl', 'rb'))
        print('f1_macro_test ->', gs.cv_results_['mean_test_f1_macro'][gs.best_index_])
        print('f1_macro_train ->', gs.cv_results_['mean_train_f1_macro'][gs.best_index_])
        print('f1_micro_test ->', gs.cv_results_['mean_test_f1_micro'][gs.best_index_])
        print('f1_micro_train ->', gs.cv_results_['mean_train_f1_micro'][gs.best_index_])

Acetylides
Alkaloids and derivatives
all
LogisticRegression(max_iter=5000, n_jobs=1, random_state=41, tol=1e-06)
sel
LogisticRegression(max_iter=5000, n_jobs=1, random_state=41, tol=1e-06)
Allenes
Benzenoids
all
LogisticRegression(max_iter=5000, n_jobs=1, random_state=41, tol=1e-06)
sel
LogisticRegression(max_iter=5000, n_jobs=1, random_state=41, tol=1e-06)
Homogeneous metal compounds
all
LogisticRegression(max_iter=5000, n_jobs=1, random_state=41, tol=1e-06)
sel
LogisticRegression(max_iter=5000, n_jobs=1, random_state=41, tol=1e-06)
Homogeneous non-metal compounds
all
LogisticRegression(max_iter=5000, n_jobs=1, random_state=41, tol=1e-06)
sel
LogisticRegression(max_iter=5000, n_jobs=1, random_state=41, tol=1e-06)
Hydrocarbon derivatives
all
LogisticRegression(max_iter=5000, n_jobs=1, random_state=41, tol=1e-06)
sel
LogisticRegression(max_iter=5000, n_jobs=1, random_state=41, tol=1e-06)
Hydrocarbons
all
LogisticRegression(max_iter=5000, n_jobs=1, random_state=41, tol=1e-06)
sel
Logisti

### SVM

In [109]:
grid = [{'penalty': ['l1', 'l2'],
        'C': [0.01, 0.1, 1, 10, 100],
        'class_weight': [None, 'balanced']}]

In [ ]:
for i, sclass in enumerate(sclasses):
    print(sclass)
    if sclass in sc_u:
        print('Only one subchild')
        continue
    for f_sel in ['all', 'sel']:
        print(f_sel)
        if f_sel == 'sel':
            sel_f = pickle.load(open('Results/selected_features.pkl', 'rb'))['Class'][sclass]['selected features']
            f_index = [feature_names.index(feature) for feature in sel_f]
            X_train_ = X_train_scal[y_train[:, classif_level-1]==sclass][:, f_index]
        else:
            X_train_ = X_train_scal[y_train[:, classif_level-1]==sclass]
            
        y_train_ = y_train[y_train[:, classif_level-1]==sclass][:, classif_level]
        
        estimator = LinearSVC(dual=False, loss='squared_hinge', multi_class='ovr', tol=1e-6, max_iter=5000, 
                              random_state=seed, verbose=3)
        gs = GridSearchCV(estimator, param_grid=grid, scoring=['f1_macro', 'f1_micro'], refit='f1_macro', cv=3, verbose=3, 
                          error_score='raise', return_train_score=True, n_jobs=-1)
        gs.fit(X_train_, y_train_)
        pickle.dump(gs, open(f'Models/Class/{i}_SVM_{f_sel}_feat.pkl', 'wb'))

Fitting 3 folds for each of 120 candidates, totalling 360 fits
[LibLinear]...........................................................*.................................*.**
optimization finished, #iter = 937
Objective value = 136.926595
#nonzeros/#features = 34/134
......*.*
optimization finished, #iter = 71
Objective value = 85.989347
#nonzeros/#features = 9/134
..........................*
optimization finished, #iter = 265
Objective value = 8.426337
#nonzeros/#features = 3/134
...............................................*..............**
optimization finished, #iter = 614
Objective value = 229.604142
#nonzeros/#features = 41/134
[CV 1/3] END C=0.5, class_weight=None, loss=squared_hinge, penalty=l1, tol=1e-06; f1_macro: (train=0.631, test=0.597) f1_micro: (train=0.887, test=0.862) total time=   0.0s
[LibLinear].........................................................*...................................*.*.**.
optimization finished, #iter = 950
Objective value = 134.938174
#nonzeros/

[CV 1/3] END C=0.5, class_weight=None, loss=squared_hinge, penalty=l1, tol=0.01; f1_macro: (train=0.627, test=0.597) f1_micro: (train=0.885, test=0.862) total time=   0.0s
[LibLinear]..............*..***.***
optimization finished, #iter = 179
Objective value = 134.942045
#nonzeros/#features = 40/134
......*
optimization finished, #iter = 66
Objective value = 87.192953
#nonzeros/#features = 9/134
.......................*
optimization finished, #iter = 231
Objective value = 10.681987
#nonzeros/#features = 3/134
.......*.*
optimization finished, #iter = 84
Objective value = 229.784847
#nonzeros/#features = 38/134
[CV 2/3] END C=0.5, class_weight=None, loss=squared_hinge, penalty=l1, tol=0.01; f1_macro: (train=0.638, test=0.587) f1_micro: (train=0.892, test=0.848) total time=   0.0s
[LibLinear].............*..**.*.**.*
optimization finished, #iter = 181
Objective value = 139.838714
#nonzeros/#features = 37/134
.....*
optimization finished, #iter = 52
Objective value = 84.956816
#nonzeros/#

[CV 2/3] END C=0.5, class_weight=None, loss=squared_hinge, penalty=l2, tol=0.0001; f1_macro: (train=0.629, test=0.565) f1_micro: (train=0.882, test=0.831) total time=   0.0s
[LibLinear]iter  1 act 1.610e+02 pre 1.610e+02 delta 6.125e-01 f 3.555e+02 |g| 5.258e+02 CG   1
cg reaches trust region boundary
iter  2 act 1.754e+01 pre 1.754e+01 delta 2.149e+00 f 1.945e+02 |g| 3.340e+01 CG   1
cg reaches trust region boundary
iter  3 act 3.349e+01 pre 3.285e+01 delta 2.566e+00 f 1.770e+02 |g| 4.121e+01 CG   2
cg reaches trust region boundary
iter  4 act 1.466e+01 pre 1.669e+01 delta 2.566e+00 f 1.435e+02 |g| 1.248e+01 CG   2
iter  5 act 4.899e+00 pre 4.856e+00 delta 2.566e+00 f 1.288e+02 |g| 7.340e+00 CG   5
iter  6 act 5.552e-02 pre 5.508e-02 delta 2.566e+00 f 1.239e+02 |g| 9.174e-01 CG   5
iter  7 act 1.230e-03 pre 1.238e-03 delta 2.566e+00 f 1.238e+02 |g| 9.247e-02 CG   6
iter  1 act 1.629e+02 pre 1.495e+02 delta 5.215e+00 f 3.555e+02 |g| 3.405e+02 CG   2
iter  2 act 3.448e+01 pre 3.315e+01 

/home/hsilva/anaconda3/lib/python3.9/site-packages/sklearn/svm/_base.py:1206: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/home/hsilva/anaconda3/lib/python3.9/site-packages/sklearn/svm/_base.py:1206: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(


.......**
optimization finished, #iter = 86
Objective value = 86.110633
#nonzeros/#features = 9/134
................................................................................................................................................................*........................................
optimization finished, #iter = 2000

Objective value = 87.988599
#nonzeros/#features = 8/134
.......................................*.........................*.*.**
optimization finished, #iter = 666
Objective value = 162.214714
#nonzeros/#features = 30/134
[CV 2/3] END C=0.5, class_weight=balanced, loss=squared_hinge, penalty=l1, tol=1e-06; f1_macro: (train=0.697, test=0.635) f1_micro: (train=0.848, test=0.825) total time=   0.0s
[LibLinear]...............................................*.............................*..*
optimization finished, #iter = 788
Objective value = 177.326561
#nonzeros/#features = 40/134
.......*.*.*
optimization finished, #iter = 94
Objective value = 83.977962
#n

...

[CV 2/3] END C=1, class_weight=balanced, loss=squared_hinge, penalty=l1, tol=0.001; f1_macro: (train=0.341, test=0.326) f1_micro: (train=0.799, test=0.798) total time= 4.5min
[LibLinear]........................................................................................................................................................................................................
optimization finished, #iter = 2000

Objective value = 2246.715936
#nonzeros/#features = 21/134
........................................................................................................................................................................................................
optimization finished, #iter = 2000

Objective value = 19183.810606
#nonzeros/#features = 17/134
........................................................................................................................................................................................................
optimization finis

/home/hsilva/anaconda3/lib/python3.9/site-packages/sklearn/svm/_base.py:1206: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(


[CV 3/3] END C=1, class_weight=balanced, loss=squared_hinge, penalty=l1, tol=0.001; f1_macro: (train=0.348, test=0.329) f1_micro: (train=0.801, test=0.801) total time= 4.2min
[LibLinear]........................................................................................................................................................................................................
optimization finished, #iter = 2000

Objective value = 1221.922689
#nonzeros/#features = 15/134
........................................................................................................................................................................................................
optimization finished, #iter = 2000

Objective value = 18850.199876
#nonzeros/#features = 19/134
........................................................................................................................................................................................................
optimization finis

/home/hsilva/anaconda3/lib/python3.9/site-packages/sklearn/svm/_base.py:1206: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(


[CV 1/3] END C=1, class_weight=balanced, loss=squared_hinge, penalty=l1, tol=0.01; f1_macro: (train=0.352, test=0.352) f1_micro: (train=0.800, test=0.799) total time= 3.3min
[LibLinear]........................................................................................................................................................................................................
optimization finished, #iter = 2000

Objective value = 2335.505063
#nonzeros/#features = 18/134
........................................................................................................................................................................................................
optimization finished, #iter = 2000

Objective value = 18931.526829
#nonzeros/#features = 19/134
........................................................................................................................................................................................................
optimization finish

In [101]:
for i, sclass in enumerate(sclasses):
    print(sclass)
    if sclass in sc_u:
        continue
    for f_sel in ['all', 'sel']:
        print(f_sel)
        gs = pickle.load(open(f'Models/Class/{i}_SVM_{f_sel}_feat.pkl', 'rb'))
        print('f1_macro_test ->', gs.cv_results_['mean_test_f1_macro'][gs.best_index_])
        print('f1_macro_train ->', gs.cv_results_['mean_train_f1_macro'][gs.best_index_])
        print('f1_micro_test ->', gs.cv_results_['mean_test_f1_micro'][gs.best_index_])
        print('f1_micro_train ->', gs.cv_results_['mean_train_f1_micro'][gs.best_index_])

Inorganic compounds
all
f1_macro_test -> 0.716551993742165
f1_macro_train -> 0.7936446310560731
f1_micro_test -> 0.8874373582317876
f1_micro_train -> 0.9338635658300483
sel
f1_macro_test -> 0.6999053599325878
f1_macro_train -> 0.7795503460699429
f1_micro_test -> 0.8696128079337448
f1_micro_train -> 0.9179156514332125
Organic compounds
all
f1_macro_test -> 0.3461317653347035
f1_macro_train -> 0.35864172077871226
f1_micro_test -> 0.7990065197143744
f1_micro_train -> 0.799844768705371
sel
f1_macro_test -> 0.3461684033085339
f1_macro_train -> 0.3586372626656141
f1_micro_test -> 0.8013505122632724
f1_micro_train -> 0.8018834730414985


### ComplementNB

In [19]:
grid = {'alpha': [0.00001, 0.0001, 0.001, 0.01, 0.1, 1, 10, 100], 
        'norm': [True, False]}

In [20]:
for i, sclass in enumerate(sclasses):
    print(sclass)
    if sclass in sc_u:
        print('Only one subchild')
        continue
    for f_sel in ['all', 'sel']:
        print(f_sel)
        if f_sel == 'sel':
            sel_f = pickle.load(open('Results/selected_features.pkl', 'rb'))['Class'][sclass]['selected features']
            f_index = [feature_names.index(feature) for feature in sel_f]
            X_train_ = X_train_scal[y_train[:, classif_level-1]==sclass][:, f_index]
        else:
            X_train_ = X_train_scal[y_train[:, classif_level-1]==sclass]
            
        y_train_ = y_train[y_train[:, classif_level-1]==sclass][:, classif_level]
        
        estimator = ComplementNB()
        gs = GridSearchCV(estimator, param_grid=grid, scoring=['f1_macro', 'f1_micro'], refit='f1_macro', cv=3, verbose=3, 
                          error_score='raise', return_train_score=True, n_jobs=-1)
        gs.fit(X_train_, y_train_)
        pickle.dump(gs, open(f'Models/Class/{i}_NB_{f_sel}_feat.pkl', 'wb'))

Acetylides
Only one subchild
Alkaloids and derivatives
all
Fitting 3 folds for each of 16 candidates, totalling 48 fits
sel
Fitting 3 folds for each of 16 candidates, totalling 48 fits
Allenes
Only one subchild
Benzenoids
all
Fitting 3 folds for each of 16 candidates, totalling 48 fits
sel
Fitting 3 folds for each of 16 candidates, totalling 48 fits
Homogeneous metal compounds
all
Fitting 3 folds for each of 16 candidates, totalling 48 fits
sel
Fitting 3 folds for each of 16 candidates, totalling 48 fits
Homogeneous non-metal compounds
all
Fitting 3 folds for each of 16 candidates, totalling 48 fits
sel
Fitting 3 folds for each of 16 candidates, totalling 48 fits
Hydrocarbon derivatives
all
Fitting 3 folds for each of 16 candidates, totalling 48 fits
sel
Fitting 3 folds for each of 16 candidates, totalling 48 fits
Hydrocarbons
all
Fitting 3 folds for each of 16 candidates, totalling 48 fits
sel
Fitting 3 folds for each of 16 candidates, totalling 48 fits
Lignans, neolignans and related

In [21]:
for i, sclass in enumerate(sclasses):
    print(sclass)
    if sclass in sc_u:
        continue
    for f_sel in ['all', 'sel']:
        print(f_sel)
        gs = pickle.load(open(f'Models/Class/{i}_NB_{f_sel}_feat.pkl', 'rb'))
        print('f1_macro_test ->', gs.cv_results_['mean_test_f1_macro'][gs.best_index_])
        print('f1_macro_train ->', gs.cv_results_['mean_train_f1_macro'][gs.best_index_])
        print('f1_micro_test ->', gs.cv_results_['mean_test_f1_micro'][gs.best_index_])
        print('f1_micro_train ->', gs.cv_results_['mean_train_f1_micro'][gs.best_index_])

Acetylides
Alkaloids and derivatives
all
f1_macro_test -> 0.060828220424975876
f1_macro_train -> 0.06474593328640532
f1_micro_test -> 0.32234432234432236
f1_micro_train -> 0.3250915750915751
sel
f1_macro_test -> 0.05068504892294321
f1_macro_train -> 0.06272954675383759
f1_micro_test -> 0.3076923076923077
f1_micro_train -> 0.3191391941391941
Allenes
Benzenoids
all
f1_macro_test -> 0.07738770262228868
f1_macro_train -> 0.08319078844809684
f1_micro_test -> 0.65237532032328
f1_micro_train -> 0.6538044549576187
sel
f1_macro_test -> 0.0636420167419503
f1_macro_train -> 0.06557721160688
f1_micro_test -> 0.35432682830672185
f1_micro_train -> 0.35531243839936916
Homogeneous metal compounds
all
f1_macro_test -> 0.9666192562852819
f1_macro_train -> 1.0
f1_micro_test -> 0.9703425229741018
f1_micro_train -> 1.0
sel
f1_macro_test -> 0.9666192562852819
f1_macro_train -> 1.0
f1_micro_test -> 0.9703425229741018
f1_micro_train -> 1.0
Homogeneous non-metal compounds
all
f1_macro_test -> 0.502958423273632

### Load GS scores

In [6]:
scores_df = []
params_df = []
for i, sclass in enumerate(sclasses):
    if sclass in sc_u:
        continue
    #Select if result is better with or without f selection
    scores_rows = [{'Classifier':sclass, 'F1-score average': 'macro'}, {'Classifier':sclass, 'F1-score average': 'micro'}]
    params_row = {'Classifier':sclass}
    for alg in ['RF', 'KNN', 'LR', 'SVM', 'NB']:
        f_sel_gs = {}
        for f_sel in ['all', 'sel']:
            f_sel_gs[f_sel] = pickle.load(open(f'Models/Class/{i}_{alg}_{f_sel}_feat.pkl', 'rb'))
        score_all = f_sel_gs['all'].cv_results_[f'mean_test_f1_macro'][f_sel_gs['all'].best_index_]
        score_sel = f_sel_gs['sel'].cv_results_[f'mean_test_f1_macro'][f_sel_gs['sel'].best_index_]
        if score_all >= score_sel:
            f_sel = 'all'
            f = 'No'
        else:
            f_sel = 'sel'
            f = 'Yes'
        gs = f_sel_gs[f_sel]
        #Save scores
        scores_rows[0][f'{alg} (val)'] = gs.cv_results_[f'mean_test_f1_macro'][gs.best_index_]
        scores_rows[0][f'{alg} (train)'] = gs.cv_results_[f'mean_train_f1_macro'][gs.best_index_]
        scores_rows[1][f'{alg} (val)'] = gs.cv_results_[f'mean_test_f1_micro'][gs.best_index_]
        scores_rows[1][f'{alg} (train)'] = gs.cv_results_[f'mean_train_f1_micro'][gs.best_index_]
        #Save parameters
        params = gs.cv_results_['params'][gs.best_index_]
        params_row[f'{alg} (Feature Selection)'] = f
        for param_name, param in params.items():
            params_row[f'{alg} ({param_name})'] = param
    scores_df.extend(scores_rows)
    params_df.append(params_row)    
scores_df = pd.DataFrame(scores_df).set_index(['Classifier', 'F1-score average'])
params_df = pd.DataFrame(params_df).set_index(['Classifier'])

In [7]:
with pd.ExcelWriter('Results/GS_scores.xlsx', mode='a') as writer:  
    scores_df.to_excel(writer, sheet_name='Class')
scores_df

RF (val)  \
Classifier                                F1-score average             
Alkaloids and derivatives                 macro             0.407087   
                                          micro             0.616300   
Benzenoids                                macro             0.360679   
                                          micro             0.712300   
Homogeneous metal compounds               macro             0.994319   
                                          micro             0.994152   
Homogeneous non-metal compounds           macro             0.681312   
                                          micro             0.693794   
Hydrocarbon derivatives                   macro             0.911111   
                                          micro             0.916667   
Hydrocarbons                              macro             0.691107   
                                          micro             0.883987   
Lignans, neolignans and related compounds macro             0.553068   
                                          micro             0.671235   
Lipids and lipid-like molecules           macro             0.743441   
                                          micro             0.948411   
Mixed metal/non-metal compounds           macro             0.739756   
                                          micro             0.828179   
Nucleosides, nucleotides, and analogues   macro             0.580836   
                                          micro             0.810681   
Organic 1,3-dipolar compounds             macro             0.962393   
                                          micro             0.984848   
Organic Polymers                          macro             1.000000   
                                          micro             1.000000   
Organic acids and derivatives             macro             0.575606   
                                          micro             0.886015   
Organic oxygen compounds                  macro             0.598250   
                                          micro             0.987769   
Organohalogen compounds                   macro             0.707571   
                                          micro             0.734272   
Organoheterocyclic compounds              macro             0.245783   
                                          micro             0.315963   
Organometallic compounds                  macro             1.000000   
                                          micro             1.000000   
Organophosphorus compounds                macro             0.810053   
                                          micro             0.851852   
Organosulfur compounds                    macro             0.476288   
                                          micro             0.669462   
Phenylpropanoids and polyketides          macro             0.426700   
                                          micro             0.684961   

                                                            RF (train)  \
Classifier                                F1-score average               
Alkaloids and derivatives                 macro               0.837875   
                                          micro               0.902473   
Benzenoids                                macro               0.835925   
                                          micro               0.909028   
Homogeneous metal compounds               macro               1.000000   
                                          micro               1.000000   
Homogeneous non-metal compounds           macro               0.971090   
                                          micro               0.967440   
Hydrocarbon derivatives                   macro               0.971484   
                                          micro               0.971618   
Hydrocarbons                              macro               0.837636   
                                          micro               0.923203   

In [8]:
with pd.ExcelWriter('Results/GS_best_comb_params.xlsx', mode='a') as writer:  
    params_df.to_excel(writer, sheet_name='Class')
params_df

RF (Feature Selection)  \
Classifier                                                         
Alkaloids and derivatives                                    Yes   
Benzenoids                                                   Yes   
Homogeneous metal compounds                                   No   
Homogeneous non-metal compounds                               No   
Hydrocarbon derivatives                                      Yes   
Hydrocarbons                                                  No   
Lignans, neolignans and related compounds                     No   
Lipids and lipid-like molecules                              Yes   
Mixed metal/non-metal compounds                               No   
Nucleosides, nucleotides, and analogues                      Yes   
Organic 1,3-dipolar compounds                                 No   
Organic Polymers                                              No   
Organic acids and derivatives                                Yes   
Organic oxygen compounds                                     Yes   
Organohalogen compounds                                       No   
Organoheterocyclic compounds                                  No   
Organometallic compounds                                      No   
Organophosphorus compounds                                    No   
Organosulfur compounds                                       Yes   
Phenylpropanoids and polyketides                              No   

                                            RF (class_weight) RF (criterion)  \
Classifier                                                                     
Alkaloids and derivatives                                None           gini   
Benzenoids                                 balanced_subsample        entropy   
Homogeneous metal compounds                              None           gini   
Homogeneous non-metal compounds            balanced_subsample        entropy   
Hydrocarbon derivatives                              balanced           gini   
Hydrocarbons                                         balanced        entropy   
Lignans, neolignans and related compounds                None        entropy   
Lipids and lipid-like molecules                          None        entropy   
Mixed metal/non-metal compounds                          None           gini   
Nucleosides, nucleotides, and analogues    balanced_subsample        entropy   
Organic 1,3-dipolar compounds                            None           gini   
Organic Polymers                                         None           gini   
Organic acids and derivatives                            None        entropy   
Organic oxygen compounds                             balanced        entropy   
Organohalogen compounds                                  None           gini   
Organoheterocyclic compounds               balanced_subsample        entropy   
Organometallic compounds                                 None        entropy   
Organophosphorus compounds                           balanced           gini   
Organosulfur compounds                               balanced        entropy   
Phenylpropanoids and polyketides                         None           gini   

                                           RF (max_features)  \
Classifier                                                     
Alkaloids and derivatives                                 13   
Benzenoids                                                34   
Homogeneous metal compounds                                1   
Homogeneous non-metal compounds                           20   
Hydrocarbon derivatives                                    1   
Hydrocarbons                                             110   
Lignans, neolignans and related compounds                100   
Lipids and lipid-like molecules                           23   
Mixed metal/non-metal compounds                            7   
Nucleosides, nucleotides, and analogues                   27   
Organic 1,3-dipo